In [1]:
import os
import re
import json
import huggingface_hub

from tqdm import tqdm
from openai import OpenAI

from langchain.schema import Document

from matplotlib import font_manager, rc
font_path = '/usr/share/fonts/truetype/nanum/NanumGothic.ttf'
font = font_manager.FontProperties(fname = font_path).get_name()
rc('font', family = font)

from dotenv import load_dotenv
load_dotenv("../keys.env")

openai_api_key = os.getenv('OPENAI_API_KEY')
os.environ['OPENAI_API_KEY'] = openai_api_key

hf_token = os.getenv("HF_TOKEN")
huggingface_hub.login(hf_token)

The token has not been saved to the git credentials helper. Pass `add_to_git_credential=True` in this function directly or `--add-to-git-credential` if using via `huggingface-cli` if you want to set the git credential as well.
Token is valid (permission: read).
Your token has been saved to /home/pervinco/.cache/huggingface/token
Login successful


In [2]:
client = OpenAI()
model = "gpt-4o"

In [3]:
def load_jsonl(file_path):
    with open(file_path, 'r', encoding='utf-8') as f:
        return [json.loads(line) for line in f]

def load_document(path="../dataset/labeled_documents.jsonl"):
    raw_documents = load_jsonl(path)

    documents = []
    for doc in raw_documents:
        doc_id = doc['docid']
        content = doc['content']

        documents.append(Document(page_content=content, metadata={"docid": doc_id}))

    return documents

In [4]:
def clean_json_response(response):
    # 코드 블록(예: ```json, ```) 제거
    cleaned_response = re.sub(r'```(?:json)?', '', response).strip()
    return cleaned_response

def translate_ko2en_doc(document, model:str, client:OpenAI):
    prompt = (
        "당신은 한국어를 영어로 번역하는 전문가입니다."
        "주어진 한국어 문서를 읽고 나서 가장 최고 품질의 영어 문서로 번역해야 합니다."
        "반환하는 형식은 반드시 JSON 포맷이어야 하며, 모든 문자열은 쌍따옴표로 감싸야 합니다. "
        "형식은 다음과 같아야 합니다: "
        '{ "translated_doc": "번역한 문서 내용" }. '

    )

    completion = client.chat.completions.create(
        model=model,
        messages=[
            {"role" : "system", "content" : prompt},
            {"role" : "user", "content" : document}
        ],
    )
    
    response = completion.choices[0].message.content
    response = clean_json_response(response)

    # 응답 내용을 로그로 출력하여 디버깅
    # print("API Response:", response)
    
    try:
        json_response = json.loads(response)
    except json.JSONDecodeError:
        return {"error": "Invalid JSON response", "response": response}
    
    # translated_doc 키가 없을 경우 에러 처리
    if "translated_doc" not in json_response:
        return {"error": "'translated_doc' key not found", "response": response}
    
    return json_response


In [5]:
def process_documents(documents, model, client, output_path='../dataset/en_4.0_documents.jsonl'):
    with open(output_path, 'w', encoding='utf-8') as outfile:
        for idx, doc in enumerate(documents):
            print(f"{idx:04}")
            print(doc.metadata['docid'])

            ko_content = doc.page_content
            translated = translate_ko2en_doc(ko_content, model, client)
            print(ko_content)
            
            # translated_doc이 없을 경우 예외 처리
            if "translated_doc" not in translated:
                print(f"Error: 'translated_doc' key not found for document {doc.metadata['docid']}")
                continue  # 오류가 발생한 문서는 스킵

            en_content = translated["translated_doc"]
            print(en_content, '\n')
                
            # 새로운 문서 구조
            en_document = {
                "docid": doc.metadata["docid"],
                "content": en_content,
                "ko_content" : ko_content
            }
                
            json.dump(en_document, outfile, ensure_ascii=False)
            outfile.write('\n')

In [6]:
# Load all documents
documents = load_document(path="../dataset/labeled_documents.jsonl")

# Get the 997th document
document = documents[997]  # 인덱스는 0부터 시작하므로 996번째가 997번째 문서

# Translate the 997th document
translated_document = translate_ko2en_doc(document.page_content, model, client)

# 결과 출력
print("원본 문서:", document.page_content)
print("번역 문서:", translated_document)


원본 문서: 셰기는 최근에 매장된 여성을 파내고 그녀와 성관계를 갖는 것에 대한 환상을 갖고 있습니다. 이러한 환상을 친구들에게 말했고, 그들은 그에게 치료를 받을 것을 권해주었습니다. 이 치료의 일환으로 셰기는 자신의 환상에 맞춰 자위를 하게 됩니다. 그리고 오르가즘 직전에는 살아있는 여성과 성관계를 가지는 환상으로 전환됩니다. 이러한 절차는 오르가즘 재조건화의 일부입니다.
번역 문서: {'translated_doc': 'Shegi recently has had fantasies about exhuming a buried woman and having sexual intercourse with her. He shared these fantasies with friends, and they recommended that he seek therapy. As part of this therapy, Shegi engages in masturbation aligned with his fantasies. Just before reaching orgasm, he shifts his imagination to having sexual relations with a living woman. This procedure is part of orgasm reconditioning.'}


In [7]:
documents = load_document()
process_documents(documents, model, client)

0000
42508ee0-c543-4338-878e-d98c6babee66
건강한 사람이 에너지 균형을 평형 상태로 유지하는 것은 중요합니다. 에너지 균형은 에너지 섭취와 에너지 소비의 수학적 동등성을 의미합니다. 일반적으로 건강한 사람은 1-2주의 기간 동안 에너지 균형을 달성합니다. 이 기간 동안에는 올바른 식단과 적절한 운동을 통해 에너지 섭취와 에너지 소비를 조절해야 합니다. 식단은 영양가 있는 식품을 포함하고, 적절한 칼로리를 섭취해야 합니다. 또한, 운동은 에너지 소비를 촉진시키고 근육을 강화시킵니다. 이렇게 에너지 균형을 유지하면 건강을 유지하고 비만이나 영양 실조와 같은 문제를 예방할 수 있습니다. 따라서 건강한 사람은 에너지 균형을 평형 상태로 유지하는 것이 중요하며, 이를 위해 1-2주의 기간 동안 식단과 운동을 조절해야 합니다.
It is important for a healthy person to maintain energy balance in equilibrium. Energy balance signifies the mathematical equivalence of energy intake and energy expenditure. Generally, a healthy person achieves energy balance over a period of 1-2 weeks. During this period, one must regulate energy intake and energy expenditure through a proper diet and appropriate exercise. A diet should include nutritious foods and an intake of adequate calories. Additionally, exercise promotes energy expenditure and strengthens muscles. Maintaining energy balance in this way helps ma

In [9]:
file_path_1 = '../dataset/en_4.0_documents.jsonl'
file_path_2 = '../dataset/documents.jsonl'

# Initialize lists to store docids from both files
docid_set_1 = set()
docid_set_2 = set()

# Load en_4.0_documents.jsonl and extract docids
with open(file_path_1, 'r', encoding='utf-8') as file_1:
    for line in file_1:
        doc = json.loads(line)
        docid_set_1.add(doc.get('docid'))

# Load documents.jsonl and extract docids
with open(file_path_2, 'r', encoding='utf-8') as file_2:
    for line in file_2:
        doc = json.loads(line)
        docid_set_2.add(doc.get('docid'))

# Find missing docids in en_4.0_documents.jsonl
missing_docids = docid_set_2 - docid_set_1

len_missing_docids = len(missing_docids)
print(len_missing_docids)
print(missing_docids)

1
{'826540a7-4c30-4a2d-b115-e452fd4350c2'}


In [11]:
file_3_5_path = '../dataset/en_3.5_document.jsonl'
file_4_0_path = '../dataset/en_4.0_document.jsonl'
missing_docid = '826540a7-4c30-4a2d-b115-e452fd4350c2'

# 3.5 버전 파일에서 해당 문서 찾기
missing_document = None
with open(file_3_5_path, 'r', encoding='utf-8') as file_3_5:
    for line in file_3_5:
        doc = json.loads(line)
        if doc.get('docid') == missing_docid:
            missing_document = doc
            break

# 4.0 버전 파일에 해당 문서 추가
if missing_document:
    with open(file_4_0_path, 'a', encoding='utf-8') as file_4_0:
        file_4_0.write(json.dumps(missing_document) + '\n')
    print(f"docid가 {missing_docid}인 문서를 en_4.0_documents.jsonl에 추가했습니다.")
else:
    print(f"docid가 {missing_docid}인 문서를 en_3.5_documents.jsonl에서 찾을 수 없습니다.")

docid가 826540a7-4c30-4a2d-b115-e452fd4350c2인 문서를 en_4.0_documents.jsonl에 추가했습니다.


In [3]:
def load_jsonl(file_path):
    with open(file_path, 'r', encoding='utf-8') as f:
        return [json.loads(line) for line in f]

In [16]:
def translate_ko2en_text(text, model: str, client: OpenAI):
    prompt = (
        "당신은 한국어를 영어로 번역하는 전문가입니다."
        "주어진 한국어 문장을 읽고 나서 가장 최고 품질의 영어 문장으로 번역해야 합니다."
    )

    completion = client.chat.completions.create(
        model=model,
        messages=[
            {"role": "system", "content": prompt},
            {"role": "user", "content": text}
        ],
    )

    response = completion.choices[0].message.content
    try:
        return response.strip()  # 번역된 문장만 반환
    except Exception as e:
        return {"error": str(e), "response": response}

In [17]:
def process_query(queries, model, client, output_path='../dataset/en_eval.jsonl'):
    with open(output_path, 'w', encoding='utf-8') as outfile:
        for idx, query in enumerate(queries):
            eval_id = query['eval_id']
            msg = query['msg']
            
            translated_msg = []
            for m in msg:
                role = m['role']
                ko_content = m['content']
                
                # 한국어 문장을 영어로 번역
                translated_content = translate_ko2en_text(ko_content, model, client)
                if isinstance(translated_content, dict) and "error" in translated_content:
                    print(f"Error in translation for eval_id {eval_id}: {translated_content['error']}")
                    continue  # 오류가 발생한 문서는 스킵
                
                # 번역된 내용을 기존 구조에 맞게 저장
                translated_msg.append({
                    "role": role,
                    "content": translated_content
                })
            
            # 새로운 문서 구조
            en_query = {
                "eval_id": eval_id,
                "msg": translated_msg
            }
            
            json.dump(en_query, outfile, ensure_ascii=False)
            outfile.write('\n')

In [18]:
queries = load_jsonl("../dataset/eval.jsonl")
process_query(queries, model, client)